In [40]:
import os
import os.path
import glob
from PIL import Image
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold                                                                                                                       
from sklearn.metrics import confusion_matrix,accuracy_score
import matplotlib.pyplot as plt
import matplotlib.cm as colormap
%matplotlib inline

import numpy as np
np.random.seed(1)

import random
from skimage import io
import cv2
from keras.preprocessing.image import img_to_array
from vis.utils import utils
from vis.visualization import visualize_cam,visualize_saliency

from keras import backend as K
from keras.utils import np_utils
from keras.utils.data_utils import get_file
from keras.preprocessing import image
from keras.applications import VGG16
from keras.applications.imagenet_utils import preprocess_input
from keras.applications.imagenet_utils import _obtain_input_shape
from keras.callbacks import ModelCheckpoint
from keras.models import Sequential,Model
from keras.layers import Input,Flatten,Dense,Dropout,GlobalAveragePooling2D,Conv2D,MaxPooling2D
from keras.optimizers import RMSprop, SGD

In [2]:
imagedir = "CG_Resized"

In [3]:
cur_dir = os.getcwd()
os.chdir(imagedir)  # the parent folder with sub-folders

# Get number of samples per family
list_fams = sorted(os.listdir(os.getcwd()), key=str.lower)  # vector of strings with family names
no_imgs = []  # No. of samples per family
for i in range(len(list_fams)):
    os.chdir(list_fams[i])
    len1 = len(glob.glob('*.jpg'))  # assuming the images are stored as 'jpg'
    no_imgs.append(len1)
    os.chdir('..')
num_samples = np.sum(no_imgs)  # total number of all samples

# Compute the labels
y = np.zeros(num_samples)
pos = 0
label = 0
for i in no_imgs:
    print ("Label:%2d\tFamily: %15s\tNumber of images: %d" % (label, list_fams[label], i))
    for j in range(i):
        y[pos] = label
        pos += 1
    label += 1
num_classes = label

# Compute the features
width, height,channels = (224,224,3)
X = np.zeros((num_samples, width, height, channels))
cnt = 0
list_paths = [] # List of image paths
print("Processing images ...")
for i in range(len(list_fams)):
    for img_file in glob.glob(list_fams[i]+'/*.jpg'):
        #print("[%d] Processing image: %s" % (cnt, img_file))
        list_paths.append(os.path.join(os.getcwd(),img_file))
        img = image.load_img(img_file, target_size=(224, 224))
        x = image.img_to_array(img)
        x = np.expand_dims(x, axis=0)
        x = preprocess_input(x)
        X[cnt] = x
        cnt += 1
print("Images processed: %d" %(cnt))

os.chdir(cur_dir)

Label: 0	Family:              CG	Number of images: 8394
Label: 1	Family:            FOTO	Number of images: 8002
Processing images ...
Images processed: 16396


In [4]:
X.shape

(16396, 224, 224, 3)

In [5]:
# Encoding classes (y) into integers (y_encoded) and then generating one-hot-encoding (Y)
encoder = LabelEncoder()
encoder.fit(y)
y_encoded = encoder.transform(y)
Y = np_utils.to_categorical(y_encoded)

In [6]:
filename = "cg-X_16396x224x224x3.npy"
if not os.path.exists(filename):
    print("Saving file %s ..." %(filename))
    np.save(filename, X)

Saving file cg-X_9339x224x224x3.npy ...


In [7]:
filename = "cg-y_numclass.npy"
if not os.path.exists(filename):
    print("Saving file %s ..." %(filename))
    np.save(filename, y)

Saving file cg-y_numclass.npy ...


In [8]:
filename = "cg-Y_onehotencode.npy"
if not os.path.exists(filename):
    print("Saving file %s ..." %(filename))
    np.save(filename, Y)

Saving file cg-Y_onehotencode.npy ...


In [9]:
# Creating base model (VGG16 convolutional layers)
img_shape = (224, 224, 3)                                                                                                                                               
model = Sequential()

# Block 1
model.add(Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv1', input_shape=img_shape))
model.add(Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv2'))
model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block1_pool'))

# Block 2
model.add(Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv1'))
model.add(Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv2'))
model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block2_pool'))

# Block 3
model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv1'))
model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv2'))
model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv3'))
model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block3_pool'))

# Block 4
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv1'))
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv2'))
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv3'))
model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block4_pool'))

# Block 5
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv1'))
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv2'))
model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv3'))
model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block5_pool'))

model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['accuracy'])       

In [10]:
vgg16weights = "vgg16_weights_tf_dim_ordering_tf_kernels.h5"
model.load_weights(vgg16weights, by_name=True)

In [11]:
filename = 'cg-vgg16features.npy'
if os.path.exists(filename):
    print("Loading VGG16 extracted features from %s ..." %(filename))
    vggfeatures = np.load(filename)
else:
    print("Extracting features from VGG16 convolutional layers ...")
    vggfeatures = model.predict(X)
    print("Saving VGG16 extracted features into %s ..." %(filename))
    np.save(filename, vggfeatures)

Extracting features from VGG16 convolutional layers ...
Saving VGG16 extracted features into cg-vgg16features.npy ...


In [12]:
# Create stratified k-fold subsets                                                                                                                                        
kfold = 10  # no. of folds                                                                 
skf = StratifiedKFold(kfold, shuffle=True,random_state=1)
skfind = [None] * kfold  # skfind[i][0] -> train indices, skfind[i][1] -> test indices
cnt = 0                                              
for index in skf.split(X, y):         
    skfind[cnt] = index                                                 
    cnt += 1 

In [13]:
# Training top_model and saving min training loss weights
num_epochs=200
history = []
conf_mat = np.zeros((len(list_fams),len(list_fams))) # Initializing the Confusion Matrix
checkpointer = ModelCheckpoint(filepath='cg-top-weights-min_loss-mlp-vgg16-2layers-160neurons-relu-0.4dropout-Adam-200epochs.h5', monitor='loss', verbose=0, save_best_only=True, save_weights_only=True, mode='min')
for i in range(kfold):
    train_indices = skfind[i][0]
    test_indices = skfind[i][1]
    X_train = vggfeatures[train_indices]
    Y_train = Y[train_indices]
    X_test = vggfeatures[test_indices]
    Y_test = Y[test_indices]
    y_test = y[test_indices]

    top_model = Sequential() 
    top_model.add(Flatten(input_shape=model.output_shape[1:])) # input_shape=(7,7,512)                                                
    top_model.add(Dense(160, activation='relu', name='fc1'))
    top_model.add(Dropout(0.4))                
    top_model.add(Dense(160, activation='relu', name='fc2'))
    top_model.add(Dropout(0.4))              
    top_model.add(Dense(num_classes, activation='softmax', name='predictions'))                             
    top_model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['accuracy'])

    h = top_model.fit(X_train, Y_train, validation_data=(X_test, Y_test), epochs=num_epochs, batch_size=X_train.shape[0], verbose=1, callbacks=[checkpointer])
    history.append(h)
    
    y_prob = top_model.predict(X_test, verbose=0)  # Testing
    y_pred = np.argmax(y_prob, axis=1)
    print("[%d] Test acurracy: %.4f" %(i,accuracy_score(y_test,y_pred)))
    cm = confusion_matrix(y_test,y_pred)  # Compute confusion matrix for this fold
    conf_mat = conf_mat + cm  # Compute global confusion matrix

Train on 14755 samples, validate on 1641 samples
Epoch 1/200
14755/14755 [==============================] - 3s - loss: 5.5283 - acc: 0.4882 - val_loss: 6.8211 - val_acc: 0.5369
Epoch 2/200
14755/14755 [==============================] - 2s - loss: 6.5285 - acc: 0.5530 - val_loss: 4.4369 - val_acc: 0.6849
Epoch 3/200
14755/14755 [==============================] - 3s - loss: 4.4566 - acc: 0.6795 - val_loss: 2.3957 - val_acc: 0.8196
Epoch 4/200
14755/14755 [==============================] - 3s - loss: 2.8239 - acc: 0.7889 - val_loss: 2.8906 - val_acc: 0.8013
Epoch 5/200
14755/14755 [==============================] - 2s - loss: 3.2343 - acc: 0.7702 - val_loss: 2.6243 - val_acc: 0.8166
Epoch 6/200
14755/14755 [==============================] - 2s - loss: 2.9695 - acc: 0.7916 - val_loss: 2.3264 - val_acc: 0.8367
Epoch 7/200
14755/14755 [==============================] - 2s - loss: 2.4524 - acc: 0.8247 - val_loss: 2.2045 - val_acc: 0.8495
Epoch 8/200
14755/14755 [==============================

14755/14755 [==============================] - 2s - loss: 0.0385 - acc: 0.9864 - val_loss: 0.5366 - val_acc: 0.9360
Epoch 128/200
14755/14755 [==============================] - 2s - loss: 0.0394 - acc: 0.9862 - val_loss: 0.5373 - val_acc: 0.9360
Epoch 129/200
14755/14755 [==============================] - 3s - loss: 0.0368 - acc: 0.9860 - val_loss: 0.5385 - val_acc: 0.9360
Epoch 130/200
14755/14755 [==============================] - 3s - loss: 0.0387 - acc: 0.9863 - val_loss: 0.5398 - val_acc: 0.9360
Epoch 131/200
14755/14755 [==============================] - 2s - loss: 0.0369 - acc: 0.9861 - val_loss: 0.5408 - val_acc: 0.9348
Epoch 132/200
14755/14755 [==============================] - 2s - loss: 0.0356 - acc: 0.9879 - val_loss: 0.5433 - val_acc: 0.9342
Epoch 133/200
14755/14755 [==============================] - 2s - loss: 0.0370 - acc: 0.9877 - val_loss: 0.5467 - val_acc: 0.9336
Epoch 134/200
14755/14755 [==============================] - 2s - loss: 0.0375 - acc: 0.9869 - val_loss:

14755/14755 [==============================] - 2s - loss: 0.0903 - acc: 0.9569 - val_loss: 0.4171 - val_acc: 0.9275
Epoch 54/200
14755/14755 [==============================] - 2s - loss: 0.0868 - acc: 0.9569 - val_loss: 0.4246 - val_acc: 0.9269
Epoch 55/200
14755/14755 [==============================] - 2s - loss: 0.0853 - acc: 0.9566 - val_loss: 0.4279 - val_acc: 0.9269
Epoch 56/200
14755/14755 [==============================] - 2s - loss: 0.0837 - acc: 0.9596 - val_loss: 0.4299 - val_acc: 0.9281
Epoch 57/200
14755/14755 [==============================] - 2s - loss: 0.0797 - acc: 0.9591 - val_loss: 0.4324 - val_acc: 0.9275
Epoch 58/200
14755/14755 [==============================] - 2s - loss: 0.0815 - acc: 0.9571 - val_loss: 0.4365 - val_acc: 0.9257
Epoch 59/200
14755/14755 [==============================] - 2s - loss: 0.0803 - acc: 0.9592 - val_loss: 0.4412 - val_acc: 0.9250
Epoch 60/200
14755/14755 [==============================] - 2s - loss: 0.0797 - acc: 0.9578 - val_loss: 0.4453

14755/14755 [==============================] - 2s - loss: 0.0395 - acc: 0.9800 - val_loss: 0.5515 - val_acc: 0.9330
Epoch 180/200
14755/14755 [==============================] - 3s - loss: 0.0390 - acc: 0.9776 - val_loss: 0.5539 - val_acc: 0.9330
Epoch 181/200
14755/14755 [==============================] - 2s - loss: 0.0374 - acc: 0.9796 - val_loss: 0.5554 - val_acc: 0.9342
Epoch 182/200
14755/14755 [==============================] - 2s - loss: 0.0387 - acc: 0.9781 - val_loss: 0.5578 - val_acc: 0.9348
Epoch 183/200
14755/14755 [==============================] - 2s - loss: 0.0391 - acc: 0.9793 - val_loss: 0.5598 - val_acc: 0.9354
Epoch 184/200
14755/14755 [==============================] - 2s - loss: 0.0398 - acc: 0.9780 - val_loss: 0.5592 - val_acc: 0.9348
Epoch 185/200
14755/14755 [==============================] - 2s - loss: 0.0385 - acc: 0.9782 - val_loss: 0.5548 - val_acc: 0.9348
Epoch 186/200
14755/14755 [==============================] - 3s - loss: 0.0368 - acc: 0.9793 - val_loss:

14756/14756 [==============================] - 2s - loss: 0.0461 - acc: 0.9734 - val_loss: 0.5243 - val_acc: 0.9305
Epoch 105/200
14756/14756 [==============================] - 2s - loss: 0.0435 - acc: 0.9736 - val_loss: 0.5301 - val_acc: 0.9299
Epoch 106/200
14756/14756 [==============================] - 2s - loss: 0.0438 - acc: 0.9734 - val_loss: 0.5357 - val_acc: 0.9293
Epoch 107/200
14756/14756 [==============================] - 2s - loss: 0.0459 - acc: 0.9735 - val_loss: 0.5419 - val_acc: 0.9287
Epoch 108/200
14756/14756 [==============================] - 2s - loss: 0.0429 - acc: 0.9749 - val_loss: 0.5507 - val_acc: 0.9293
Epoch 109/200
14756/14756 [==============================] - 2s - loss: 0.0424 - acc: 0.9749 - val_loss: 0.5580 - val_acc: 0.9287
Epoch 110/200
14756/14756 [==============================] - 2s - loss: 0.0456 - acc: 0.9742 - val_loss: 0.5662 - val_acc: 0.9287
Epoch 111/200
14756/14756 [==============================] - 2s - loss: 0.0440 - acc: 0.9753 - val_loss:

...

14757/14757 [==============================] - 2s - loss: 0.0413 - acc: 0.9761 - val_loss: 0.6819 - val_acc: 0.9268
Epoch 184/200
14757/14757 [==============================] - 2s - loss: 0.0390 - acc: 0.9774 - val_loss: 0.6886 - val_acc: 0.9256
Epoch 185/200
14757/14757 [==============================] - 2s - loss: 0.0374 - acc: 0.9775 - val_loss: 0.6909 - val_acc: 0.9243
Epoch 186/200
14757/14757 [==============================] - 2s - loss: 0.0409 - acc: 0.9762 - val_loss: 0.6923 - val_acc: 0.9243
Epoch 187/200
14757/14757 [==============================] - 2s - loss: 0.0405 - acc: 0.9780 - val_loss: 0.6937 - val_acc: 0.9243
Epoch 188/200
14757/14757 [==============================] - 2s - loss: 0.0405 - acc: 0.9773 - val_loss: 0.6937 - val_acc: 0.9243
Epoch 189/200
14757/14757 [==============================] - 2s - loss: 0.0381 - acc: 0.9794 - val_loss: 0.6935 - val_acc: 0.9250
Epoch 190/200
14757/14757 [==============================] - 2s - loss: 0.0383 - acc: 0.9785 - val_loss:

14757/14757 [==============================] - 2s - loss: 0.0468 - acc: 0.9755 - val_loss: 0.5737 - val_acc: 0.9280
Epoch 109/200
14757/14757 [==============================] - 2s - loss: 0.0442 - acc: 0.9778 - val_loss: 0.5734 - val_acc: 0.9280
Epoch 110/200
14757/14757 [==============================] - 2s - loss: 0.0467 - acc: 0.9768 - val_loss: 0.5743 - val_acc: 0.9274
Epoch 111/200
14757/14757 [==============================] - 2s - loss: 0.0463 - acc: 0.9774 - val_loss: 0.5770 - val_acc: 0.9268
Epoch 112/200
14757/14757 [==============================] - 2s - loss: 0.0465 - acc: 0.9774 - val_loss: 0.5788 - val_acc: 0.9274
Epoch 113/200
14757/14757 [==============================] - 3s - loss: 0.0439 - acc: 0.9774 - val_loss: 0.5836 - val_acc: 0.9268
Epoch 114/200
14757/14757 [==============================] - 2s - loss: 0.0426 - acc: 0.9792 - val_loss: 0.5869 - val_acc: 0.9256
Epoch 115/200
14757/14757 [==============================] - 2s - loss: 0.0442 - acc: 0.9778 - val_loss:

14757/14757 [==============================] - 2s - loss: 0.1348 - acc: 0.9258 - val_loss: 0.3933 - val_acc: 0.9067
Epoch 34/200
14757/14757 [==============================] - 3s - loss: 0.1282 - acc: 0.9292 - val_loss: 0.4095 - val_acc: 0.9054
Epoch 35/200
14757/14757 [==============================] - 2s - loss: 0.1212 - acc: 0.9318 - val_loss: 0.4215 - val_acc: 0.9067
Epoch 36/200
14757/14757 [==============================] - 2s - loss: 0.1186 - acc: 0.9335 - val_loss: 0.4278 - val_acc: 0.9079
Epoch 37/200
14757/14757 [==============================] - 2s - loss: 0.1154 - acc: 0.9345 - val_loss: 0.4330 - val_acc: 0.9085
Epoch 38/200
14757/14757 [==============================] - 2s - loss: 0.1105 - acc: 0.9370 - val_loss: 0.4385 - val_acc: 0.9097
Epoch 39/200
14757/14757 [==============================] - 2s - loss: 0.1098 - acc: 0.9370 - val_loss: 0.4448 - val_acc: 0.9121
Epoch 40/200
14757/14757 [==============================] - 2s - loss: 0.1033 - acc: 0.9408 - val_loss: 0.4546

14757/14757 [==============================] - 2s - loss: 0.0349 - acc: 0.9791 - val_loss: 0.6847 - val_acc: 0.9250
Epoch 160/200
14757/14757 [==============================] - 2s - loss: 0.0356 - acc: 0.9806 - val_loss: 0.6863 - val_acc: 0.9262
Epoch 161/200
14757/14757 [==============================] - 3s - loss: 0.0347 - acc: 0.9796 - val_loss: 0.6860 - val_acc: 0.9256
Epoch 162/200
14757/14757 [==============================] - 3s - loss: 0.0337 - acc: 0.9791 - val_loss: 0.6825 - val_acc: 0.9262
Epoch 163/200
14757/14757 [==============================] - 2s - loss: 0.0356 - acc: 0.9773 - val_loss: 0.6774 - val_acc: 0.9262
Epoch 164/200
14757/14757 [==============================] - 2s - loss: 0.0335 - acc: 0.9808 - val_loss: 0.6726 - val_acc: 0.9292
Epoch 165/200
14757/14757 [==============================] - 2s - loss: 0.0329 - acc: 0.9803 - val_loss: 0.6686 - val_acc: 0.9292
Epoch 166/200
14757/14757 [==============================] - 2s - loss: 0.0367 - acc: 0.9778 - val_loss:

14757/14757 [==============================] - 2s - loss: 0.0597 - acc: 0.9653 - val_loss: 0.5558 - val_acc: 0.9250
Epoch 85/200
14757/14757 [==============================] - 2s - loss: 0.0595 - acc: 0.9650 - val_loss: 0.5573 - val_acc: 0.9243
Epoch 86/200
14757/14757 [==============================] - 2s - loss: 0.0607 - acc: 0.9662 - val_loss: 0.5588 - val_acc: 0.9243
Epoch 87/200
14757/14757 [==============================] - 2s - loss: 0.0612 - acc: 0.9663 - val_loss: 0.5607 - val_acc: 0.9237
Epoch 88/200
14757/14757 [==============================] - 2s - loss: 0.0601 - acc: 0.9658 - val_loss: 0.5624 - val_acc: 0.9231
Epoch 89/200
14757/14757 [==============================] - 2s - loss: 0.0572 - acc: 0.9684 - val_loss: 0.5647 - val_acc: 0.9250
Epoch 90/200
14757/14757 [==============================] - 2s - loss: 0.0569 - acc: 0.9669 - val_loss: 0.5688 - val_acc: 0.9250
Epoch 91/200
14757/14757 [==============================] - 2s - loss: 0.0572 - acc: 0.9670 - val_loss: 0.5710

In [14]:
# Computing the average accuracy
avg_acc = np.trace(conf_mat)/sum(no_imgs)
print("Average acurracy: %.4f" %(avg_acc))

Average acurracy: 0.9303


In [15]:
def plot_acc(history):
    figure = plt.gcf()
    figure.set_size_inches(24, 9)
    ax = plt.subplot()
    plt.title('Accuracy')
    plt.ylabel('Accuracy')
    plt.xlabel('Epoch')
    colors = iter(colormap.gist_rainbow(np.linspace(0, 1, len(history))))
    for i in range(len(history)):
        color=next(colors)
        plt.plot(history[i].history['acc'], label='Train '+str(i), color=color, linestyle = 'solid')
        plt.plot(history[i].history['val_acc'], label='Test '+str(i), color=color, linestyle = 'dotted')
    x1,x2,y1,y2 = plt.axis()
    plt.axis((x1,x2,0.0,1.0))
    plt.legend()
    box = ax.get_position()
    ax.set_position([box.x0, box.y0, box.width * 0.8, box.height])
    ax.legend(loc='center left', bbox_to_anchor=(1, 0.5))
    plt.grid(True)
    plt.show()

In [16]:
def plot_loss(history):
    figure = plt.gcf()
    figure.set_size_inches(24, 9)
    ax = plt.subplot()
    plt.title('Loss')
    plt.ylabel('Loss')
    plt.xlabel('Epoch')
    colors = iter(colormap.gist_rainbow(np.linspace(0, 1, len(history))))
    for i in range(len(history)):
        color=next(colors)
        plt.plot(history[i].history['loss'], label='Train '+str(i), color=color, linestyle = 'solid')
        plt.plot(history[i].history['val_loss'], label='Test '+str(i), color=color, linestyle = 'dotted')
    plt.legend()
    box = ax.get_position()
    ax.set_position([box.x0, box.y0, box.width * 0.8, box.height])
    ax.legend(loc='center left', bbox_to_anchor=(1, 0.5))
    plt.grid(True)
    plt.show()

In [17]:
plot_acc(history)

In [18]:
plot_loss(history)

In [19]:
# Viewing the confusion matrix
conf_mat = conf_mat.T  # since rows and cols are interchangeable
conf_mat_norm = conf_mat/no_imgs  # Normalizing the confusion matrix

In [20]:
print("Plotting the confusion matrix")
conf_mat = np.around(conf_mat_norm,decimals=2)  # rounding to display in figure
figure = plt.gcf()
figure.set_size_inches(24, 18)
plt.imshow(conf_mat,interpolation='nearest')
for row in range(len(list_fams)):
    for col in range(len(list_fams)):
        plt.annotate(str(conf_mat[row][col]),xy=(col,row),ha='center',va='center')
plt.xticks(range(len(list_fams)),list_fams,rotation=90,fontsize=10)
plt.yticks(range(len(list_fams)),list_fams,fontsize=10)
plt.title('Confusion matrix')
plt.colorbar()
plt.show()

Plotting the confusion matrix


In [21]:
# Stacking top model (fc and softmax layers)
model.add(Flatten())                                                
model.add(Dense(160, activation='relu', name='fc1'))
model.add(Dropout(0.4))                
model.add(Dense(160, activation='relu', name='fc2'))
model.add(Dropout(0.4))              
model.add(Dense(num_classes, activation='softmax', name='predictions'))                             

In [22]:
top_weigths = "cg-top-weights-min_loss-mlp-vgg16-2layers-160neurons-relu-0.4dropout-Adam-200epochs.h5"
model.load_weights(top_weigths, by_name=True)

In [23]:
model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [24]:
# The name of the layer we want to visualize
layer_name = 'predictions'
layer_idx = [idx for idx, layer in enumerate(model.layers) if layer.name == layer_name][0]

In [38]:
for fam in list_fams:
    print("Class: %s" %(fam))
    fam_samples = [name for name in list_paths if fam in name.split('/')[-2:-1]]
    print len(fam_samples)
    image_paths = random.sample(fam_samples, 25)
    
    heatmaps = []
    for path in image_paths:
        # Predict the corresponding class for use in `visualize_cam`.
        seed_img = utils.load_img(path, target_size=(224, 224))
        pred_class = np.argmax(model.predict(np.array([img_to_array(seed_img)])))
        print("Image: %s - Class: %s - Pred: %d (%s)" %(path.split('/')[-1:],path.split('/')[-2:-1],pred_class,list_fams[pred_class]))

        # Here we are asking it to show attention such that prob of `pred_class` is maximized.
        heatmap = visualize_cam(model, layer_idx, [pred_class], seed_img, text=list_fams[pred_class])
        heatmaps.append(heatmap)
        
    img_data = cv2.cvtColor(utils.stitch_images(heatmaps), cv2.COLOR_BGR2RGB)
    plt.figure(figsize=(16, 16))
    plt.axis('off')
    plt.imshow(img_data)
    plt.show()        

Class: CG
8394
Image: ['261110_8.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['1236179369.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['1245188233.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['web_1222363896.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['landscape_58.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['1231238858.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['web_1222422524.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['cbwinter.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['salma.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['covered_courtyard.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['autumnps.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['final_living_Room_14.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['36.13305.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['432.13305.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['web_1280407783.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['612.13305.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image: ['6706.jpg'] - Class: ['CG'] - Pred: 0 (CG)
Image:

Class: FOTO
8002
Image: ['16_15_53_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['15_27_1_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['10_52_52_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['05_13_85_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['15_01_17_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['05_25_78_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['1501_09_58_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['18_36_96_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['19_38_76_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['07_02_3_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['1450_11_88_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['1218_33_20_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['14_14_8_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['2051_20_23_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['15_86_24_prev.jpg'] - Class: ['FOTO'] - Pred: 1 (FOTO)
Image: ['1215_05_8

In [ ]:
# Fine-tuning the model (base_model + top_model) 
num_epochs=5
history2 = []
conf_mat2 = np.zeros((len(list_fams),len(list_fams))) # Initializing the Confusion Matrix
checkpointer = ModelCheckpoint(filepath='cg-finetuned-weights-max_val_acc-mlp-vgg16-2layers-160neurons-relu-0.4dropout-Adam-5epochs.h5', monitor='val_acc', verbose=0, save_best_only=True, save_weights_only=True, mode='max')
for i in range(kfold):
    train_indices = skfind[i][0]
    test_indices = skfind[i][1]
    X_train = X[train_indices]
    Y_train = Y[train_indices]
    X_test = X[test_indices]
    Y_test = Y[test_indices]
    y_test = y[test_indices]

    # Creating base model (VGG16 convolutional layers)
    img_shape = (224, 224, 3)                                                                                                                                               
    model = Sequential()
    # Block 1
    model.add(Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv1', input_shape=img_shape))
    model.add(Conv2D(64, (3, 3), activation='relu', padding='same', name='block1_conv2'))
    model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block1_pool'))
    # Block 2
    model.add(Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv1'))
    model.add(Conv2D(128, (3, 3), activation='relu', padding='same', name='block2_conv2'))
    model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block2_pool'))
    # Block 3
    model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv1'))
    model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv2'))
    model.add(Conv2D(256, (3, 3), activation='relu', padding='same', name='block3_conv3'))
    model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block3_pool'))
    # Block 4
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv1'))
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv2'))
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block4_conv3'))
    model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block4_pool'))
    # Block 5
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv1'))
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv2'))
    model.add(Conv2D(512, (3, 3), activation='relu', padding='same', name='block5_conv3'))
    model.add(MaxPooling2D((2, 2), strides=(2, 2), name='block5_pool'))
    vgg16weights = "vgg16_weights_tf_dim_ordering_tf_kernels.h5"
    model.load_weights(vgg16weights, by_name=True)
    
    # Stacking top model (fc and softmax layers)
    model.add(Flatten())                                                
    model.add(Dense(160, activation='relu', name='fc1'))
    model.add(Dropout(0.4))                
    model.add(Dense(160, activation='relu', name='fc2'))
    model.add(Dropout(0.4))              
    model.add(Dense(num_classes, activation='softmax', name='predictions'))  
    top_weigths = "cg-top-weights-min_loss-mlp-vgg16-2layers-160neurons-relu-0.4dropout-Adam-200epochs.h5"
    model.load_weights(top_weigths, by_name=True)

    #model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['accuracy']) 
    model.compile(loss='categorical_crossentropy', optimizer=SGD(lr=0.0001, decay=1e-6, momentum=0.9, nesterov=True), metrics=['accuracy'])

    h2 = model.fit(X_train, Y_train, validation_data=(X_test, Y_test), epochs=num_epochs, batch_size=300, verbose=1, callbacks=[checkpointer])
    history2.append(h2)
    
    y_prob = model.predict(X_test, verbose=0)  # Testing
    y_pred = np.argmax(y_prob, axis=1)
    print("[%d] Test acurracy: %.4f" %(i,accuracy_score(y_test,y_pred)))
    cm2 = confusion_matrix(y_test,y_pred)  # Compute confusion matrix for this fold
    conf_mat2 = conf_mat2 + cm2  # Compute global confusion matrix

Train on 14755 samples, validate on 1641 samples
Epoch 1/5
 9600/14755 [==================>...........] - ETA: 4139s - loss: 0.0316 - acc: 0.9893

In [ ]:
# Computing the average accuracy
avg_acc2 = np.trace(conf_mat2)/sum(no_imgs)
print("Average acurracy: %.4f" %(avg_acc2))

In [ ]:
plot_acc(history2)

In [ ]:
plot_loss(history2)